In [1]:
import scipy.io as sio
import scipy
import numpy as np
import torch.nn as nn
import torch.nn.functional as F
import torch.optim as op
from torch.utils.data import Dataset, DataLoader, random_split
import torchvision
import os
import torchvision.transforms as tt
import torch
from torch.utils.data import Dataset
from torch.utils.data import DataLoader
import torch.nn.functional as Fun
from sklearn.model_selection import train_test_split
from sklearn.metrics import confusion_matrix
import seaborn as sn
import pandas as pd
import matplotlib.pyplot as plt
from torchvision import transforms
from pytorchtools import EarlyStopping 
import random
import cv2
from PIL import Image
from model import U2NET
from tqdm import tqdm

def random_seed(seed):
    if torch.backends.cudnn.enabled:
        torch.backends.cudnn.benchmark = False
        torch.backends.cudnn.deterministic = True

    torch.manual_seed(seed)
    torch.cuda.manual_seed(seed)
    np.random.seed(seed)
    random.seed(seed)
    print('Using GPU : ', torch.cuda.is_available() , ' |  Seed : ', seed)

torch.multiprocessing.set_start_method('spawn')
os.environ["CUDA_DEVICE_ORDER"]="PCI_BUS_ID"  # Arrange GPU devices starting from 0
os.environ["CUDA_VISIBLE_DEVICES"]= "0,1,2"  # Set the GPU 0 to use
NGPU = torch.cuda.device_count()
DEVICE = torch.device("cuda" if torch.cuda.is_available() else "cpu")
# DEVICE = torch.device('cuda:1' if torch.cuda.is_available() else 'cpu') 
print(f'9. Selected device: {DEVICE}')
print('Current cuda device:', torch.cuda.current_device())
print('Count of using GPUs:', torch.cuda.device_count())

random_seed(0)
early_stopping = EarlyStopping(patience = 10, verbose = True)
tx_total = []
rx_total = []

for i in tqdm(range(-10, 4)):
    rx = sio.loadmat('/home2/siho0201/lab/radar_gen/dataset/SNR' + str(i * 2))
    tx_total.extend(rx['LFMD']['tx'][0:270])
    tx_total.extend(rx['Costas']['tx'][0:270])
    tx_total.extend(rx['Barker']['tx'][0:270])
    tx_total.extend(rx['Frank']['tx'][0:270])
    tx_total.extend(rx['P1']['tx'][0:270])
    tx_total.extend(rx['P2']['tx'][0:270])
    tx_total.extend(rx['P3']['tx'][0:270])
    tx_total.extend(rx['P4']['tx'][0:270])
    tx_total.extend(rx['T1']['tx'][0:270])
    tx_total.extend(rx['T2']['tx'][0:270])
    tx_total.extend(rx['T3']['tx'][0:270])
    tx_total.extend(rx['T4']['tx'][0:270])

    rx_total.extend(rx['LFMD']['rx'][0:270])
    rx_total.extend(rx['Costas']['rx'][0:270])
    rx_total.extend(rx['Barker']['rx'][0:270])
    rx_total.extend(rx['Frank']['rx'][0:270])
    rx_total.extend(rx['P1']['rx'][0:270])
    rx_total.extend(rx['P2']['rx'][0:270])
    rx_total.extend(rx['P3']['rx'][0:270])
    rx_total.extend(rx['P4']['rx'][0:270])
    rx_total.extend(rx['T1']['rx'][0:270])
    rx_total.extend(rx['T2']['rx'][0:270])
    rx_total.extend(rx['T3']['rx'][0:270])
    rx_total.extend(rx['T4']['rx'][0:270])
X = []
for i in tqdm(range(len(rx_total))):
    X.extend(rx_total[i][0])
Y = []
for i in tqdm(range(len(rx_total))):
    Y.extend(tx_total[i][0])    

thresh = 135
maxValue = 255 

for i in range(0,len(Y)):
  ori = Y[i]
  ori = ori*1.2 / np.max(ori)
  ori = np.exp(ori)
  ori = np.uint8(255 * ori/ np.max(ori))
  th, dst = cv2.threshold(ori, -1, 255,  cv2.THRESH_BINARY | cv2.THRESH_OTSU)
  Y[i] = dst
# Y[0]
# image1 = Image.fromarray(np.uint8(Y[1]))
# image1.show()
X = np.array(X)
Y = np.array(Y)
X = X.reshape(-1,1,256,256)
Y = Y.reshape(-1,1,256,256)



# print(LFM.shape)
# print(X.shape)

class Train_data(Dataset): 
  def __init__(self):
    self.x_data = X
    self.y_data = Y
   
    # self.y_data = [[0],[1],[2],[3],[4],[5],[6],[7],[8],[9],[10],[11]]

 
  def __len__(self): 
    return len(self.x_data)

  def __getitem__(self, idx): 
    x = self.x_data[idx].astype(np.float32)
    y = self.y_data[idx].astype(np.float32)
    x = x/255
    y = y/255

    x = torch.tensor(x,dtype = torch.float32)
    y = torch.tensor(y,dtype = torch.float32)
    # x = Fun.normalize(x,p=2,dim=1)
    # y = Fun.normalize(y,p=2,dim=1)
    # print(x)
    # print(y)
    # y = Fun.one_hot(y,num_classes =4)
    return x, y

train_dataset = Train_data()
# transform = transforms.Compose([transforms.Normalize(mean=0.5,std=0.5)])
batch_size = 32
trainloader = DataLoader(train_dataset, batch_size=batch_size, shuffle=True)



/home2/siho0201/anaconda3/envs/dl/lib/python3.8/site-packages/tqdm/auto.py:22: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


9. Selected device: cuda
Current cuda device: 0
Count of using GPUs: 3
Using GPU :  True  |  Seed :  0


100%|██████████| 168/168 [00:00<00:00, 22026.98it/s]


In [2]:
print(X.shape)
print(Y.shape)

(50400, 1, 256, 256)
(50400, 1, 256, 256)


In [3]:
bce_loss = nn.BCELoss(size_average=True)
net = U2NET(1,1)
if (DEVICE.type == 'cuda') and (torch.cuda.device_count() > 1):
    print('Multi GPU activate')
    net = nn.DataParallel(net, device_ids = list(range(NGPU)))
net.to(DEVICE)
optimizer = op.Adam(net.parameters(), lr=0.001, betas=(0.9, 0.999), eps=1e-08, weight_decay=0)

def muti_bce_loss_fusion(d0, d1, d2, d3, d4, d5, d6, labels_v):

	loss0 = bce_loss(d0,labels_v)
	loss1 = bce_loss(d1,labels_v)
	loss2 = bce_loss(d2,labels_v)
	loss3 = bce_loss(d3,labels_v)
	loss4 = bce_loss(d4,labels_v)
	loss5 = bce_loss(d5,labels_v)
	loss6 = bce_loss(d6,labels_v)

	loss = loss0 + loss1 + loss2 + loss3 + loss4 + loss5 + loss6
	print("l0: %3f, l1: %3f, l2: %3f, l3: %3f, l4: %3f, l5: %3f, l6: %3f\n"%(loss0.data.item(),loss1.data.item(),loss2.data.item(),loss3.data.item(),loss4.data.item(),loss5.data.item(),loss6.data.item()))

	return loss0, loss

def saveModel():
    path = "./U2net.pth"
    torch.save(net.state_dict(),path)

epoch_num = 1000
batch_size_train = 16
batch_size_val = 1
train_num = 0
val_num = 0

ite_num = 0
running_loss = 0.0
running_tar_loss = 0.0
ite_num4val = 0
save_frq = 2000 # save the model every 2000 iterations

print("----------------------Train start------------------------")
for epoch in range(0,epoch_num):
	net.train  # Train loop
	for data in trainloader:
		ite_num = ite_num + 1
		ite_num4val = ite_num4val + 1
		train_inputs, train_labels = data
		# print(train_inputs)
		train_inputs = train_inputs.to(DEVICE) 
		train_labels = train_labels.to(DEVICE) 
		optimizer.zero_grad() 
		# print(train_inputs.size())
		# print(train_labels.size())
		d0, d1, d2, d3, d4, d5, d6  = net(train_inputs) 
		# print(outputs.size())
		loss2, loss = muti_bce_loss_fusion(d0, d1, d2, d3, d4, d5, d6, train_labels)
		loss.backward()
		optimizer.step()
		running_loss += loss.data.item()
		running_tar_loss += loss2.data.item()
		del d0, d1, d2, d3, d4, d5, d6, loss2, loss 

		print("[epoch: %3d/%3d, batch: %5d/%5d, ite: %d] train loss: %3f, tar: %3f " % (
        epoch + 1, epoch_num, (i + 1) * batch_size, train_num, ite_num, running_loss / ite_num4val, running_tar_loss / ite_num4val))
		if epoch % 5 == 0:
			saveModel()
			print('savemodel')
        	
        	

    



/home2/siho0201/anaconda3/envs/dl/lib/python3.8/site-packages/torch/nn/_reduction.py:42: UserWarning: size_average and reduce args will be deprecated, please use reduction='mean' instead.
  warnings.warn(warning.format(ret))


Multi GPU activate
----------------------Train start------------------------


/home2/siho0201/anaconda3/envs/dl/lib/python3.8/site-packages/torch/nn/functional.py:3734: UserWarning: nn.functional.upsample is deprecated. Use nn.functional.interpolate instead.
  warnings.warn("nn.functional.upsample is deprecated. Use nn.functional.interpolate instead.")
/home2/siho0201/anaconda3/envs/dl/lib/python3.8/site-packages/torch/nn/functional.py:1967: UserWarning: nn.functional.sigmoid is deprecated. Use torch.sigmoid instead.
  warnings.warn("nn.functional.sigmoid is deprecated. Use torch.sigmoid instead.")


l0: 0.543041, l1: 0.603579, l2: 0.790080, l3: 0.514765, l4: 1.210508, l5: 0.468470, l6: 0.653935

[epoch:   1/1000, batch: 1612800/    0, ite: 1] train loss: 4.784377, tar: 0.543041 
savemodel
l0: 0.999080, l1: 0.436692, l2: 0.563154, l3: 0.720229, l4: 0.798275, l5: 0.490508, l6: 0.217913

[epoch:   1/1000, batch: 1612800/    0, ite: 2] train loss: 4.505114, tar: 0.771060 
savemodel
l0: 1.106007, l1: 0.284688, l2: 0.407786, l3: 0.254134, l4: 0.219621, l5: 0.160580, l6: 0.122872

[epoch:   1/1000, batch: 1612800/    0, ite: 3] train loss: 3.855306, tar: 0.882709 
savemodel
l0: 0.617747, l1: 0.194714, l2: 0.277542, l3: 0.139724, l4: 0.159833, l5: 0.114266, l6: 0.179438

[epoch:   1/1000, batch: 1612800/    0, ite: 4] train loss: 3.312295, tar: 0.816469 
savemodel
l0: 0.294717, l1: 0.140710, l2: 0.203909, l3: 0.118595, l4: 0.104548, l5: 0.117098, l6: 0.215450

[epoch:   1/1000, batch: 1612800/    0, ite: 5] train loss: 2.888841, tar: 0.712118 
savemodel
l0: 0.181806, l1: 0.097301, l2: 0.1